In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
#!pip install sentencepiece

In [ ]:
import numpy as np
import pandas as pd
!pip install transformers
!pip install datasets
!pip install sacrebleu
!pip insall accelerate

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 45.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 107.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 200.1/200.1 kB 24.1 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 468.7/468.7 kB 8.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 18.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 24.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.9/132.9 kB 18.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.2/212.2 kB 28.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.2/114.2 kB 16.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.8/158.8 kB 24.1 MB/s eta 0:00:

In [ ]:
from datasets import load_dataset
from transformers import (
    MBartForConditionalGeneration, MBartTokenizer,
    Seq2SeqTrainingArguments, Seq2SeqTrainer
  )

import torch
from torch.utils.data import random_split
import datasets
import pandas as pd
from transformers import AutoModelForSeq2SeqLM, DataCollatorForSeq2Seq, Seq2SeqTrainingArguments, Seq2SeqTrainer
import numpy as np
from datasets import load_metric
import gc
import torch
from transformers import AutoTokenizer
import datasets

In [ ]:
train = pd.read_csv('/content/drive/MyDrive/custom_train_3_1to21.csv')
train.head()

Sentence  \
0  @someUSER congratulations on you celebrating b...   
1  @LoKarDi_RT uske liye toh bahot kuch karna pad...   
2  @slimswamy yehi to hum semjhane ki koshish kar...   
3                    @DramebaazKudi cake kaha hai ??   
4  @someUSER i'm in hawaii at the moment .  home ...   

                                 English_Translation  
0  @some users congratulate you for celebrating B...  
1  @Lokardi_ rat we should a lot more for that, b...  
2  @Slimswami ehi, this is what i'm expecting you...  
3         @Where is Dramebajakudi where is the cake?  
4  @some user Don't want to come home next friday...

In [ ]:
val = pd.read_csv('/content/drive/MyDrive/st2.csv')
val = val.rename(columns = {'Hinglish' : 'Sentence', 'English' : 'English_Translation'})
val.head()

Sentence  \
0  Abe bigg boss show me baki contestants bhi hai...   
1      Filhal toh behanchod zindagi rape kr rae hai.   
2  agar tumhare sath rape ho jaye to tumhare fath...   
3  I hate it, hostel me banti thi. Us din chawal ...   
4  Tumhare to terrorism failane aate Hain, Indian...   

                                 English_Translation  
0  Now there are other contestants in the Bigg Bo...  
1           At present the behanchod life is raping.  
2   What will your father do if Rape happens to you?  
3  I hate it. was made in hostel. that time i was...  
4  You come to spread terrorism, the Indian Army ...

In [ ]:
train = pd.concat([train, val])
train.shape

(25558, 2)

In [ ]:
train['Sentence'].info()

<class 'pandas.core.series.Series'>
Int64Index: 25558 entries, 0 to 499
Series name: Sentence
Non-Null Count  Dtype 
--------------  ----- 
25558 non-null  object
dtypes: object(1)
memory usage: 399.3+ KB


In [ ]:
train['English_Translation'].info()

<class 'pandas.core.series.Series'>
Int64Index: 25558 entries, 0 to 499
Series name: English_Translation
Non-Null Count  Dtype 
--------------  ----- 
25558 non-null  object
dtypes: object(1)
memory usage: 399.3+ KB


In [ ]:
train.dropna(inplace = True)

In [ ]:
train.shape, val.shape#, test.shape

((25558, 2), (500, 2))

In [ ]:
train_rows = train
val_rows = val

In [ ]:
def load_val():
    d = []
    for i in range(0, val_rows.shape[0]):
      src = val_rows.iloc[i, :]['Sentence']
      tgt = val_rows.iloc[i, :]['English_Translation']
      print("SRC: ", src)
      print("TRG: ", tgt)
      d.append(
              {
                  "translation": {
                      "hinglish": src.strip(),
                      "english": tgt.strip()
                  }
              }
      )
    print(f'total size of data is {len(d)}')
    tdata = pd.DataFrame(d)
    tdata = tdata.reset_index()
    tdata = tdata.rename(columns={'index': 'id'})
    dataset = datasets.Dataset.from_pandas(tdata)

    return dataset

val_set = load_val()

SRC:  Abe bigg boss show me baki contestants bhi hai un se related news deta nhi...sirf sari updates hina se related deta hai...wo bhi hate wali...khabari hai bakri chabar chabar karta rehta hina k bare me
TRG:  Now there are other contestants in the Bigg Boss show and you not giving news related to them. why all updates related to hina? that too hatted... khabri is chatting always about hina.
SRC:  Filhal toh behanchod zindagi rape kr rae hai.
TRG:  At present the behanchod life is raping.
SRC:  agar tumhare sath rape ho jaye to tumhare father kya karenge
TRG:  What will your father do if Rape happens to you?
SRC:  I hate it, hostel me banti thi. Us din chawal me ghee aur namak daal ke khati thi
TRG:  I hate it. was made in hostel. that time i was eating by mixing salt and butter in the rice.
SRC:  Tumhare to terrorism failane aate Hain, Indian army 72 hooron se mila deti unko
TRG:  You come to spread terrorism, the Indian Army would get meet 72 Hurons to them.

SRC:  100 Dino mai Boh

In [ ]:
def load_train():
    d = []
    for i in range(0, train_rows.shape[0]):
      src = train_rows.iloc[i, :]['Sentence']
      tgt = train_rows.iloc[i, :]['English_Translation']
      print("SRC: ", src)
      print("TRG: ", tgt)
      d.append(
              {
                  "translation": {
                      "hinglish": src.strip(),
                      "english": tgt.strip()
                  }
              }
      )
    print(f'total size of data is {len(d)}')
    tdata = pd.DataFrame(d)
    tdata = tdata.reset_index()
    tdata = tdata.rename(columns={'index': 'id'})
    dataset = datasets.Dataset.from_pandas(tdata)

    return dataset

train_set = load_train()

Streaming output truncated to the last 5000 lines.
You don't know about fact as yu don't know about the scientific methods
SRC:  tum raints ho 
TRG:  
You are rants
SRC:  aap ek mdhysthta pr bolte hain, jhan aap utne hi khali sind ke sath sbse apriy hain jaise aap apne moorkh sonnet aur apne bojhil gle ko pas krte haina apni ajnjanta se khush aur mshmallow ko pas krte hain 
TRG:   You speak on an arbitration where you are most unwelcome with the same empty sind as you pass your idiotic sonnet and your fat ass: happy of your ignorancy and passing the marshmallow
SRC:  iske lie main is prstav ko smrthn krta hoon. 
TRG:  

 

For what it is worth, I support this motion
SRC:  ekseel ne chrcha men kuchh yogdan nhin diya hai, Igor ya rbj ya ybm jaise any adhikansh upyogkrtaon ke viprit, aur aksr baten uljhata hai 
TRG:   XAL has contributed nothing to the discussion, in stark contraindistinction to most of the other users like Igor or rbj or ybm, and often stirs things up
SRC:  mauroo talk k

In [ ]:
val_set

Dataset({
    features: ['id', 'translation'],
    num_rows: 500
})

In [ ]:
train_set

Dataset({
    features: ['id', 'translation'],
    num_rows: 25558
})

In [ ]:
!pip install sentencepiece

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 19.9 MB/s eta 0:00:00


In [ ]:
tokenizer = AutoTokenizer.from_pretrained("facebook/mbart-large-50-many-to-many-mmt")
print(tokenizer(["Hello, this one sentence!", "This is another sentence."]))

{'input_ids': [[250004, 35378, 4, 903, 1632, 149357, 38, 2], [250004, 3293, 83, 15700, 149357, 5, 2]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1, 1]]}


In [ ]:
model = MBartForConditionalGeneration.from_pretrained("facebook/mbart-large-50-many-to-many-mmt")

In [ ]:
max_input_length = 128
max_target_length = 128
source_lang = "hinglish"
target_lang = "english"

def preprocess_function(examples):
    inputs = [ex[source_lang] for ex in examples["translation"]]
    targets = [ex[target_lang] for ex in examples["translation"]]
    model_inputs = tokenizer(inputs, max_length=max_input_length, truncation=True)
    labels = tokenizer(targets, max_length=max_target_length, truncation=True)
    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

In [ ]:
tokenized_train_set = train_set.map(preprocess_function, batched=True)

Map:   0%|          | 0/25558 [00:00<?, ? examples/s]

In [ ]:
tokenized_train_set = train_set.map(preprocess_function, batched=True)
tokenized_val_set = val_set.map(preprocess_function, batched=True)

Map:   0%|          | 0/25558 [00:00<?, ? examples/s]

Map:   0%|          | 0/500 [00:00<?, ? examples/s]

In [ ]:
tokenized_train_set['translation']

[{'english': "@some users congratulate you for celebrating British kid singers Sophia Grace's and Rosie's 1st anniversary visit of your show",
  'hinglish': "@someUSER congratulations on you celebrating british kid singers sophia grace's and rosie's 1st anniversary of a visit of your show .  how"},
 {'english': '@Lokardi_ rat we should a lot more for that, by this evi people nothing will happen #ForTheSakeOfHumanity',
  'hinglish': '@LoKarDi_RT uske liye toh bahot kuch karna padega ye pappiyon se kaam nahi chalega #ForTheSakeOfHumanity'},
 {'english': "@Slimswami ehi, this is what i'm expecting you to understand, people invest everything in this isnt it.",
  'hinglish': '@slimswamy yehi to hum semjhane ki koshish kar rahe hain. Log to sab kuch ko issi mein tol dete hain. Context:http://www.opindia.com/2015/02/buzzfeed-editor-tries-to-make-political-tweets-you-wont-believe-what-happened-next/\xa0…'},
 {'english': '@Where is Dramebajakudi where is the cake?',
  'hinglish': '@DramebaazKud

In [ ]:
data_collator = DataCollatorForSeq2Seq(tokenizer, model=model)
metric = load_metric("sacrebleu")

<ipython-input-27-b5f524766ed4>:2: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  metric = load_metric("sacrebleu")


In [ ]:
def postprocess_text(preds, labels):
    preds = [pred.strip() for pred in preds]
    labels = [[label.strip()] for label in labels]

    return preds, labels

def compute_metrics(eval_preds):
    preds, labels = eval_preds
    if isinstance(preds, tuple):
        preds = preds[0]
    decoded_preds = tokenizer.batch_decode(preds, skip_special_tokens=True)

    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)
    decoded_preds, decoded_labels = postprocess_text(decoded_preds, decoded_labels)

    result = metric.compute(predictions=decoded_preds, references=decoded_labels)
    result = {"bleu": result["score"]}

    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in preds]
    result["gen_len"] = np.mean(prediction_lens)
    result = {k: round(v, 4) for k, v in result.items()}
    return result

In [ ]:
!pip install accelerate

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 215.3/215.3 kB 5.4 MB/s eta 0:00:00


In [ ]:
from accelerate import Accelerator
accelerator = Accelerator()

In [ ]:
args = Seq2SeqTrainingArguments(output_dir="./mbart_810/",
                        do_train=True,
                        do_eval=True,
                        evaluation_strategy="epoch",
                        per_device_train_batch_size=2,
                        per_device_eval_batch_size=2,
                        learning_rate=5e-5,
                        num_train_epochs=2,
                        predict_with_generate=True,
                        logging_dir="/logs",
                        logging_steps=10000,
                        save_steps=10000,
                        report_to="none"
                        )

In [ ]:
trainer = Seq2SeqTrainer(model=model,
                args=args,
                data_collator=data_collator,
                train_dataset=tokenized_train_set,
                eval_dataset=tokenized_val_set,
                tokenizer=tokenizer,
                compute_metrics=compute_metrics
                )

tokenized_datasets, tokenized_test_set, trainer2 = accelerator.prepare(
     tokenized_train_set, tokenized_val_set, trainer
      )

trainer.train()

/usr/local/lib/python3.9/dist-packages/transformers/optimization.py:391: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
You're using a MBart50TokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=25558, training_loss=1.221597011347352, metrics={'train_runtime': 10656.7949, 'train_samples_per_second': 4.797, 'train_steps_per_second': 2.398, 'total_flos': 4304245635121152.0, 'train_loss': 1.221597011347352, 'epoch': 2.0})

In [ ]:
test = pd.read_csv('/content/drive/MyDrive/test_st2.csv')
test = test.rename(columns = {'Hinglish' : 'Sentence', 'English' : 'English_Translation'})
test.head()

Sentence  \
0  Wah Wah kya baat he par viyapam ghotale ki jaa...   
1  Kaun hai eh bhai logo iska bhi rape kardo na, ...   
2  Hindu to rape karne ke baad bhi rehta hai ek c...   
3  Ek din ayega ki tumahara hi rape hoga aur jam ...   
4  Gujarat BJP ke karyakarta ne rape Kiya he vo K...   

                                 English_Translation  
0  What is that thing? But more than 50 murders h...  
1  Who is this brother rape her too, this woman i...  
2  Hindu remains a criminal even after raped..wha...  
3  One day will come and you will be raped and wi...  
4  Gujarat BJP worker has raped. Show that news o...

In [ ]:
test_rows = test

In [ ]:
def load_test():
    d = []
    for i in range(0, test_rows.shape[0]):
      src = test_rows.iloc[i, :]['Sentence']
      tgt = test_rows.iloc[i, :]['English_Translation']
      print("SRC: ", src)
      print("TRG: ", tgt)
      d.append(
              {
                  "translation": {
                      "hinglish": src.strip(),
                      "english": tgt.strip()
                  }
              }
      )
    print(f'total size of data is {len(d)}')
    tdata = pd.DataFrame(d)
    tdata = tdata.reset_index()
    tdata = tdata.rename(columns={'index': 'id'})
    dataset = datasets.Dataset.from_pandas(tdata)

    return dataset

test_set = load_test()

SRC:  Wah Wah kya baat he par viyapam ghotale ki jaaz me 50 se jyada murder ho Gaye he . Apne tou world record Bana diya Saab. Badhai ho apko
TRG:  What is that thing? But more than 50 murders have taken place in the investigation of Viapam scam. You have made a world record, Saab. Congratulations to you
SRC:  Kaun hai eh bhai logo iska bhi rape kardo na, Bahut bechen hai eh mahila, shayed  peechlee janam ki esi icchaa hai iski.BJP k time do it https://twitter.com/SahilThoughts/status/892906767683903492 …
TRG:  Who is this brother rape her too, this woman is very restless, maybe this is the desire of her last life. Do it in BJP's time. https://twitter.com/SahilThoughts/status/892906767683903492 …
SRC:  Hindu to rape karne ke baad bhi rehta hai ek criminal..What is ur point???
TRG:  Hindu remains a criminal even after raped..what is ur point???

SRC:  Ek din ayega ki tumahara hi rape hoga aur jam kad rape hoga
TRG:  One day will come and you will be raped and will be forced raped.
SRC: 

In [ ]:
test_set

Dataset({
    features: ['id', 'translation'],
    num_rows: 1500
})

In [ ]:
tokenized_test_set = test_set.map(preprocess_function, batched=True)
tokenized_test_set = accelerator.prepare(tokenized_test_set)

Map:   0%|          | 0/1500 [00:00<?, ? examples/s]

In [ ]:
predictions = trainer.predict(tokenized_test_set)

In [ ]:
predictions.predictions

In [ ]:
import pickle as pkl

In [ ]:
with open('/content/drive/MyDrive/801_test_predictions_list_3.pkl', 'wb') as f:
  pkl.dump(predictions.predictions, f)

In [ ]:
predictions.label_ids

array([[250004,   4865,     83, ...,      1,      1,      1],
       [250004,  40469,     83, ...,      1,      1,      1],
       [250004,  83009,  47143, ...,      1,      1,      1],
       ...,
       [250004,  17779,    658, ...,      1,      1,      1],
       [250004,  67921,      4, ...,      1,      1,      1],
       [250004,    360, 115215, ...,      1,      1,      1]])

In [ ]:
predictions.metrics

{'test_loss': 1.8597537279129028,
 'test_bleu': 27.078,
 'test_gen_len': 31.5693,
 'test_runtime': 729.0489,
 'test_samples_per_second': 2.057,
 'test_steps_per_second': 1.029}

In [ ]:
tokenizer

MBart50TokenizerFast(name_or_path='facebook/mbart-large-50-many-to-many-mmt', vocab_size=250054, model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'bos_token': '<s>', 'eos_token': '</s>', 'unk_token': '<unk>', 'sep_token': '</s>', 'pad_token': '<pad>', 'cls_token': '<s>', 'mask_token': '<mask>', 'additional_special_tokens': ['ar_AR', 'cs_CZ', 'de_DE', 'en_XX', 'es_XX', 'et_EE', 'fi_FI', 'fr_XX', 'gu_IN', 'hi_IN', 'it_IT', 'ja_XX', 'kk_KZ', 'ko_KR', 'lt_LT', 'lv_LV', 'my_MM', 'ne_NP', 'nl_XX', 'ro_RO', 'ru_RU', 'si_LK', 'tr_TR', 'vi_VN', 'zh_CN', 'af_ZA', 'az_AZ', 'bn_IN', 'fa_IR', 'he_IL', 'hr_HR', 'id_ID', 'ka_GE', 'km_KH', 'mk_MK', 'ml_IN', 'mn_MN', 'mr_IN', 'pl_PL', 'ps_AF', 'pt_XX', 'sv_SE', 'sw_KE', 'ta_IN', 'te_IN', 'th_TH', 'tl_XX', 'uk_UA', 'ur_PK', 'xh_ZA', 'gl_ES', 'sl_SI']}, clean_up_tokenization_spaces=True)

In [ ]:
tokenizer.decode(predictions.predictions[0])

'</s>en_XX wow wow, there has been a lot of murder in the area of viyapam ghotale. you made a world record. congratulations to you.</s><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad>'

In [ ]:
for i in range(0, len(predictions.predictions)):
  print("Test data point number ", i)
  print("Source English: ")
  print(tokenized_test_set[i]['translation']['english'])
  print("Source Hinglish: ")
  print(tokenized_test_set[i]['translation']['hinglish'])
  print("Translation: ")
  print(tokenizer.decode(predictions.predictions[i]))
  print()

Streaming output truncated to the last 5000 lines.
Source Hinglish: 
DIYA GAYA. AUR BHI SUNIYE KI MURDER CASE MEIN BHI F.I.R. ME NAAM DARG USKE SALE, SASUR,  SAAS, KA NAAM BARABANKI KI POLICE NE 5-5 LAKH
Translation: 
</s>en_XX it's done. and even in the dead case of sunny, even in F.I.R., the law of woman was 5 lakhs.</s><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><

In [ ]:
x_test = []
y_test = []
y_pred = []
for i in range(0, len(predictions.predictions)):
  x_test.append(tokenized_test_set[i]['translation']['english'])
  y_test.append(tokenized_test_set[i]['translation']['hinglish'])
  y_pred.append(tokenizer.decode(predictions.predictions[i]))

In [ ]:
len(x_test), len(y_test), len(y_pred)

(1500, 1500, 1500)

In [ ]:
from nltk.translate.bleu_score import sentence_bleu
bleu = []
# reference and predicted sentences
for i in range(0, 1000):
  ref_sent = y_test[i].split()
  pred_sent = y_pred[i].split()
  # calculate BLEU score
  score = sentence_bleu(ref_sent, pred_sent)
  bleu.append(score)

print(bleu)

/usr/local/lib/python3.9/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.9/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.9/dist-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg

[9.788429383461836e-232, 0, 8.285726588482745e-232, 1.0244914152188952e-231, 0, 0, 9.418382295637229e-232, 0, 0, 0, 0, 8.319100378795605e-232, 0, 9.418382295637229e-232, 0, 0, 0, 0, 0, 9.109159947227211e-232, 0, 1.0518351895246305e-231, 0, 0, 0, 0, 9.594503055152632e-232, 0, 0, 0, 0, 0, 8.412065649527267e-232, 0, 0, 7.03404585427606e-232, 8.34060433022243e-232, 0, 9.418382295637229e-232, 0, 9.257324954728539e-232, 0, 0, 0, 0, 0, 9.109159947227211e-232, 9.181748633447778e-232, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8.412065649527267e-232, 0, 0, 8.147480343967206e-232, 7.337741777064293e-232, 0, 9.893133360884868e-232, 0, 0, 0, 0, 7.784451369270533e-232, 0, 0, 0, 0, 0, 0, 0, 0, 8.844844403089351e-232, 7.544641259221007e-232, 0, 8.412065649527267e-232, 0, 8.614911585158347e-232, 0, 1.0003688322288243e-231, 8.06798322521923e-232, 8.844844403089351e-232, 8.510469113101058e-232, 0, 8.510469113101058e-232, 0, 0, 0, 0, 0, 0, 0, 0, 9.788429383461836e-232, 9.788429383461836e-232, 9.418382295637229e-232, 0, 

In [ ]:
predictions.predictions

array([[     2, 250004, 104130, ...,      1,      1,      1],
       [     2, 250004,   2750, ...,      1,      1,      1],
       [     2, 250004,  83009, ...,      1,      1,      1],
       ...,
       [     2, 250004,  17779, ...,      1,      1,      1],
       [     2, 250004,  82953, ...,      1,      1,      1],
       [     2, 250004,   3853, ...,      1,      1,      1]])

In [ ]:
preds = []
for i in range(0, len(predictions.predictions)):
  d = tokenizer.decode(predictions.predictions[i])
  preds.append(d)

In [ ]:
x_test = []
for i in range(0, len(tokenized_test_set)):
  d = tokenized_test_set[i]['translation']['english']
  x_test.append(d)

In [ ]:
y_test = []
for i in range(0, len(tokenized_test_set)):
  d = tokenized_test_set[i]['translation']['hinglish']
  y_test.append(d)

In [ ]:
x_test

['What is that thing? But more than 50 murders have taken place in the investigation of Viapam scam. You have made a world record, Saab. Congratulations to you',
 "Who is this brother rape her too, this woman is very restless, maybe this is the desire of her last life. Do it in BJP's time. https://twitter.com/SahilThoughts/status/892906767683903492 …",
 'Hindu remains a criminal even after raped..what is ur point???',
 'One day will come and you will be raped and will be forced raped.',
 'Gujarat BJP worker has raped. Show that news on your news, tell that news of the country, about the Naliyakand,',
 'Hindustan is Rape and hunger is their identity.',
 'It seems that having five husbands (Draupadi) is also born from rape.',
 'And thay too by following me and by ignoring my tweets, reweets my retweetes. i hate them.',
 'Indra dev was not, was Vishnu there? Why did raped Vrinda? You do not have knowledge yourself and you are speaking to the other person.',
 'The dog rapist was from Islam

In [ ]:
preds

['</s>en_XX wow wow, there has been a lot of murder in the area of viyapam ghotale. you made a world record. congratulations to you.</s><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad>',
 '</s>en_XX who is this brother

In [ ]:
y_test

['Wah Wah kya baat he par viyapam ghotale ki jaaz me 50 se jyada murder ho Gaye he . Apne tou world record Bana diya Saab. Badhai ho apko',
 'Kaun hai eh bhai logo iska bhi rape kardo na, Bahut bechen hai eh mahila, shayed  peechlee janam ki esi icchaa hai iski.BJP k time do it https://twitter.com/SahilThoughts/status/892906767683903492\xa0…',
 'Hindu to rape karne ke baad bhi rehta hai ek criminal..What is ur point???',
 'Ek din ayega ki tumahara hi rape hoga aur jam kad rape hoga',
 'Gujarat BJP ke karyakarta ne rape Kiya he vo Khabar Chala APNI news par, desh ki Khabar bata, Naliyakand ke bare me,',
 'Hindustan hai rape aur bhok en pehchan hai',
 'lagta hai ki 5 Husbands rakhne wali (Draupadi) bhi rape ke paida hui hai',
 'or vo bhi mujhe follow karke  mere tweets ko ignore karke  rt maarte mere kiye  hue rts ko.i hate them',
 'Indra dev nahi tha vishnu to tha na?  Vrinda ka rape Kyo kiya tha?  Khud ko knowledge hai nahi aur samne valo ko bol rahe ho',
 'Kutte ka rape karne wala isl

In [ ]:
x_test

['What is that thing? But more than 50 murders have taken place in the investigation of Viapam scam. You have made a world record, Saab. Congratulations to you',
 "Who is this brother rape her too, this woman is very restless, maybe this is the desire of her last life. Do it in BJP's time. https://twitter.com/SahilThoughts/status/892906767683903492 …",
 'Hindu remains a criminal even after raped..what is ur point???',
 'One day will come and you will be raped and will be forced raped.',
 'Gujarat BJP worker has raped. Show that news on your news, tell that news of the country, about the Naliyakand,',
 'Hindustan is Rape and hunger is their identity.',
 'It seems that having five husbands (Draupadi) is also born from rape.',
 'And thay too by following me and by ignoring my tweets, reweets my retweetes. i hate them.',
 'Indra dev was not, was Vishnu there? Why did raped Vrinda? You do not have knowledge yourself and you are speaking to the other person.',
 'The dog rapist was from Islam

In [ ]:
preds

['</s>en_XX wow wow, there has been a lot of murder in the area of viyapam ghotale. you made a world record. congratulations to you.</s><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad>',
 '</s>en_XX who is this brother

In [ ]:
import pickle
with open("preds_3.pkl", "wb") as f:
    pickle.dump(preds, f)

In [ ]:
import pickle
with open("y_test_3.pkl", "wb") as f:
    pickle.dump(y_test, f)

In [ ]:
import pickle
with open("x_test_3.pkl", "wb") as f:
    pickle.dump(x_test, f)

In [ ]:
preds

['</s>en_XX wow wow, there has been a lot of murder in the area of viyapam ghotale. you made a world record. congratulations to you.</s><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad><pad>',
 '</s>en_XX who is this brother

In [ ]:
stripped_preds = []
for i in preds:
  s = i.replace("<pad>", "")
  s = s.replace("</s>", "")
  s = s.replace("en_XX", "")
  stripped_preds.append(s)

In [ ]:
stripped_preds

[' wow wow, there has been a lot of murder in the area of viyapam ghotale. you made a world record. congratulations to you.',
 ' who is this brother, rape him as well, he is very innocent, he is innocent, at the time of BJP, do it https://twitter.com/SahilThoughts/status/892906767683903492...',
 ' Hindus remain a criminal even after doing rape..what is your point???',
 ' One day it will come that there will be a rape and there will be a clock of rape.',
 " the work of gujarat bjp has done rape, that is news on abhi news, country's news, about naliyakand,",
 ' India is rape and hunk and pehchan',
 ' Looks like those who keep 5 Husbands (Draupadi) are also born from rape.',
 ' And they also follow me and ignore my tweets and retweet my kiye hue rats.i hate them',
 " Indra was not the god, was he? Why did you rape Vrinda? You don't know, you are telling the truth to everyone in front.",
 ' The dog was raped by Islam.',
 ' sweet cold is less.. delhi is rape capital even now @ashutosh83B',


In [ ]:
stripped_preds[2], x_test[2]

(' Hindus remain a criminal even after doing rape..what is your point???',
 'Hindu remains a criminal even after raped..what is ur point???')

In [ ]:
import pickle
with open("stripped_preds_3.pkl", "wb") as f:
    # Use the pickle.dump() method to pickle the data to the file
    pickle.dump(stripped_preds, f)

In [ ]:
!pip install sacrebleu

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
bleu_list = []
for i in range(len(stripped_preds)):
  references = [stripped_preds[i]]
  translations = [x_test[i]]
  bleu = sacrebleu.corpus_bleu(translations, [references])
  bleu_list.append(bleu.score)

In [ ]:
bleu_list

[10.858943671423319,
 35.26704437810992,
 43.14793368698176,
 7.964191616699299,
 6.481236440245939,
 5.669791110976001,
 30.781789741768915,
 17.12473044894657,
 11.839441618747346,
 19.64073254502566,
 14.458924666162856,
 32.03561891801426,
 4.625799890348224,
 8.23351492792295,
 24.384183193426086,
 13.134549472120788,
 10.96015488148204,
 21.88720372235159,
 54.816047830879924,
 29.11892337378931,
 9.669265690880861,
 62.33473783356552,
 16.26170171519489,
 29.5580130165708,
 3.0759934809350447,
 46.85909905380382,
 39.375553105513404,
 5.875148471810145,
 6.809398432036521,
 7.809849842300637,
 9.30524746413493,
 11.737849637633069,
 13.208842603328344,
 6.200503000840492,
 4.910716049447604,
 5.706275612661898,
 57.15564496297264,
 14.377919100088198,
 13.910732727119134,
 7.61223519170024,
 12.583171179755176,
 68.85326214539053,
 19.35950972190742,
 10.571070857151538,
 6.4790667469036025,
 3.5536559081652053,
 44.581353773440114,
 19.96574716097467,
 65.25452579142082,
 44.89

In [ ]:
np.average(bleu_list)

22.833639046970056

In [ ]:
stripped_preds[0]

' wow wow, there has been a lot of murder in the area of viyapam ghotale. you made a world record. congratulations to you.'

In [ ]:
x_test[0]

'What is that thing? But more than 50 murders have taken place in the investigation of Viapam scam. You have made a world record, Saab. Congratulations to you'

In [ ]:
trainer.save_model("/content/drive/MyDrive/my_trained_model")

In [ ]:
from transformers import Seq2SeqTrainer, Seq2SeqTrainingArguments, AutoTokenizer, AutoModelForSeq2SeqLM

tokenizer = AutoTokenizer.from_pretrained("/content/drive/MyDrive/model2.pth")
model = AutoModelForSeq2SeqLM.from_pretrained("/content/drive/MyDrive/model2.pth")
trainer_loaded = Seq2SeqTrainer(model=model, args=Seq2SeqTrainingArguments( output_dir="/content/drive/MyDrive"))

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <cell line: 3>:3                                                                              │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/transformers/models/auto/tokenization_auto.py:642 in      │
│ from_pretrained                                                                                  │
│                                                                                                  │
│   639 │   │   │   return tokenizer_class.from_pretrained(pretrained_model_name_or_path, *input   │
│   640 │   │                                                                                      │
│   641 │   │   # Next, let's try to use the tokenizer_config file to get the tokenizer class.     │
│ ❱ 642 │   │   tokenizer_config = get_tokenizer_config(pretrained_model_name_or_path, **kwargs)   │
│   643 │   │   if "_commit_hash" in tokenizer_config:                                             │
│   644 │   │   │   kwargs["_commit_hash"] = tokenizer_config["_commit_hash"]                      │
│   645 │   │   config_tokenizer_class = tokenizer_config.get("tokenizer_class")                   │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/transformers/models/auto/tokenization_auto.py:486 in      │
│ get_tokenizer_config                                                                             │
│                                                                                                  │
│   483 │   tokenizer_config = get_tokenizer_config("tokenizer-test")                              │
│   484 │   ```"""                                                                                 │
│   485 │   commit_hash = kwargs.get("_commit_hash", None)                                         │
│ ❱ 486 │   resolved_config_file = cached_file(                                                    │
│   487 │   │   pretrained_model_name_or_path,                                                     │
│   488 │   │   TOKENIZER_CONFIG_FILE,                                                             │
│   489 │   │   cache_dir=cache_dir,                                                               │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/transformers/utils/hub.py:409 in cached_file              │
│                                                                                                  │
│    406 │   user_agent = http_user_agent(user_agent)                                              │
│    407 │   try:                                                                                  │
│    408 │   │   # Load from URL or cache if already cached                                        │
│ ❱  409 │   │   resolved_file = hf_hub_download(                                                  │
│    410 │   │   │   path_or_repo_id,                                                              │
│    411 │   │   │   filename,                                                                     │
│    412 │   │   │   subfolder=None if len(subfolder) == 0 else subfolder,                         │
│                                                                                                  │
│ /usr/local/lib/python3.9/dist-packages/huggingface_hub/utils/_validators.py:112 in _inner_fn     │
│                                                                                                  │
│   109 │   │   │   kwargs.items(),  # Kwargs values                                               │
│   110 │   │   ):                                                                                 │
│   111 │   │   │   if arg_name in ["repo_id", "from_id", "to

In [ ]:
model = AutoModelForSeq2SeqLM.from_pretrained("/content/drive/MyDrive/my_trained_model")

In [ ]:
trainer_loaded = Seq2SeqTrainer(model=model, args=Seq2SeqTrainingArguments( output_dir="/content/drive/MyDrive"))

In [ ]:
model

MBartForConditionalGeneration(
  (model): MBartModel(
    (shared): Embedding(250054, 1024, padding_idx=1)
    (encoder): MBartEncoder(
      (embed_tokens): Embedding(250054, 1024, padding_idx=1)
      (embed_positions): MBartLearnedPositionalEmbedding(1026, 1024)
      (layers): ModuleList(
        (0-11): 12 x MBartEncoderLayer(
          (self_attn): MBartAttention(
            (k_proj): Linear(in_features=1024, out_features=1024, bias=True)
            (v_proj): Linear(in_features=1024, out_features=1024, bias=True)
            (q_proj): Linear(in_features=1024, out_features=1024, bias=True)
            (out_proj): Linear(in_features=1024, out_features=1024, bias=True)
          )
          (self_attn_layer_norm): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
          (activation_fn): ReLU()
          (fc1): Linear(in_features=1024, out_features=4096, bias=True)
          (fc2): Linear(in_features=4096, out_features=1024, bias=True)
          (final_layer_norm): LayerNor

In [ ]:
model.state_dict()

OrderedDict([('final_logits_bias',
              tensor([[0., 0., 0.,  ..., 0., 0., 0.]], device='cuda:0')),
             ('model.shared.weight',
              tensor([[-0.0378, -0.0182,  0.0085,  ..., -0.0523,  0.0086,  0.0099],
                      [-0.0538,  0.0387,  0.0166,  ..., -0.0357, -0.0172, -0.0175],
                      [-0.0461, -0.0337, -0.0215,  ..., -0.0419,  0.0169, -0.0120],
                      ...,
                      [-0.0518, -0.0957, -0.0159,  ..., -0.0491,  0.0045, -0.0036],
                      [-0.0457, -0.0373, -0.0034,  ..., -0.0120, -0.0402,  0.0132],
                      [-0.0487,  0.0042,  0.0089,  ..., -0.0589, -0.0229, -0.0126]],
                     device='cuda:0')),
             ('model.encoder.embed_tokens.weight',
              tensor([[-0.0378, -0.0182,  0.0085,  ..., -0.0523,  0.0086,  0.0099],
                      [-0.0538,  0.0387,  0.0166,  ..., -0.0357, -0.0172, -0.0175],
                      [-0.0461, -0.0337, -0.0215,  ..., -0.0419

In [ ]:
torch.save(model.state_dict(), '/content/drive/MyDrive/trained_model_mbart50_1.pth')

In [ ]:
model2 = MBartForConditionalGeneration.from_pretrained("facebook/mbart-large-50-many-to-many-mmt")
model2.load_state_dict(torch.load('/content/drive/MyDrive/trained_model_mbart50_1.pth'))

In [ ]:
model2